In [1]:
# 모듈 불러오기
from docx import Document
import pandas as pd

In [2]:
def extract_info(record):
    name = record["성명"]
    total = int(record["연봉총액"])
    base = int(record['기본급'])
    overtime_pay = int(record['시간외 근무수당'])
    lunch = int(record['식대'])
    overtime_month = int(record['연장시간(월)'])
    overtime_year = int(record['연장시간(연)'])
    return name, total, base, overtime_pay, lunch, overtime_month, overtime_year

In [3]:
def digit2txt(strNum):
    # 만 단위 자릿수
    tenThousandPos = 4
    # 억 단위 자릿수
    hundredMillionPos = 9
    txtDigit = ['', '십', '백', '천', '만', '억']
    txtNumber = ['', '일', '이', '삼', '사', '오', '육', '칠', '팔', '구']
    txtPoint = '쩜 '
    resultStr = ''
    digitCount = 0
    #자릿수 카운트
    for ch in strNum:
        # ',' 무시
        if ch == ',':
            continue
        #소숫점 까지
        elif ch == '.':
            break
        digitCount = digitCount + 1

    digitCount = digitCount-1
    index = 0

    while True:
        notShowDigit = False
        ch = strNum[index]
        if ch == ',':
            index = index + 1
            if index >= len(strNum):
                break;
            continue

        if ch == '.':
            resultStr = resultStr + txtPoint
        else:
            #자릿수가 2자리이고 1이면 '일'은 표시 안함.
            # 단 '만' '억'에서는 표시 함
            if(digitCount > 1) and (digitCount != tenThousandPos) and  (digitCount != hundredMillionPos) and int(ch) == 1:
                resultStr = resultStr + ''
            elif int(ch) == 0:
                resultStr = resultStr + ''
                # 단 '만' '억'에서는 표시 함
                if (digitCount != tenThousandPos) and  (digitCount != hundredMillionPos):
                    notShowDigit = True
            else:
                resultStr = resultStr + txtNumber[int(ch)]

        # 1억 이상
        if digitCount > hundredMillionPos:
            if not notShowDigit:
                resultStr = resultStr + txtDigit[digitCount-hundredMillionPos]
        # 1만 이상
        elif digitCount > tenThousandPos:
            if not notShowDigit:
                resultStr = resultStr + txtDigit[digitCount-tenThousandPos]
        else:
            if not notShowDigit:
                resultStr = resultStr + txtDigit[digitCount]

        if digitCount <= 0:
            digitCount = 0
        else:
            digitCount = digitCount - 1
        index = index + 1
        if index >= len(strNum):
            break;
            
    return(resultStr)

In [22]:
doc = Document('2022 연봉계약서_양식.docx')
for i, para in enumerate(doc.paragraphs):
    print(i, para.text)

0 연 봉 계 약 서
1 
2 
3  A사(이하 ‘갑’이라 한다)와 근로자     (이하 ‘을’이라 한다)은(는) 아래와 같이 ‘갑’이 ‘을’에게 1년간 지급할 연봉계약을 체결한다.
4 
5 1. 계약기간 : 2022년  1 월  1일부터 2022년  12 월  31 일까지
6 
7 2. 연봉금액 
8 2-1. 연봉총액 : 금    원(￦        )
9 2-2. 연봉구성
10 


In [11]:
data = pd.read_excel("직원연봉.xlsx")
for _, record in data.iterrows():
    doc = Document('2022 연봉계약서_양식.docx')
    name, total, base, overtime_pay, lunch, overtime_month, overtime_year = extract_info(record) # 직원 정보 가져오기
    
    # 이름 추가
    para = doc.paragraphs[3]
    para.text = para.text.replace("근로자     ", "근로자 {} ".format(' '.join(name)))
    
    # 연봉 총액 추가
    para = doc.paragraphs[8]
    para.text = para.text.replace("(￦        )", "(￦{:,})".format(total))
    para.text = para.text.replace('금    원', '금 {}원'.format(digit2txt(str(total))))
    
    # 날짜 추가
    para = doc.tables[0].rows[1].cells[0].paragraphs[1]
    para.text = para.text.replace("2022.    .    .", "2022.01.14")
    
    # 서약인 추가
    para = doc.tables[0].rows[1].cells[0].paragraphs[2]
    para.text = para.text.replace(":        (인)", ": {} (인)".format(' '.join(name)))
    
    # 기본급 추가
    doc.tables[1].rows[1].cells[2].paragraphs[0].text = "￦" + "{:,}".format(base)
    
    # 시간 외 근무 수당 추가
    doc.tables[1].rows[2].cells[2].paragraphs[0].text = "￦" + "{:,}".format(overtime_pay)
    
    # 연장 시간 추가
    para = doc.tables[1].rows[2].cells[3].paragraphs[0]
    para.text = para.text.replace("월    시간, 연     시간 근로", "월 {}시간, 연 {}시간 근로".format(overtime_month, overtime_year))
    
    # 중식대 보조금 추가
    doc.tables[1].rows[3].cells[2].paragraphs[0].text = "￦" + "{:,}".format(lunch)
    
    # 합계 추가
    doc.tables[1].rows[4].cells[2].paragraphs[0].text = "￦" + "{:,}".format(total)
    doc.save("연봉계약서_{}.docx".format(name))